 Organizar arquivos por Ano.
 Copia os arquivos e adiciona na pasta do respectivo ano ao que o arquivo foi criado. Organiza os arquivos e copia a estrutura de diretórios que contém os arquivos.

In [1]:
# -*- coding: UTF-8 -*-

In [2]:
#Importa as bibliotecas necessárias
import datetime
import os
import shutil
import time

In [3]:
#Define o endereço de origem dos arquivos.
#path_origem = 'C:\\Users\\charlessodre\\Documents\\PastaVM\\Estudos\\OrganizadorArquivos\\source_img'
path_origem = 'C:\\BACKUPS_FOTOS_CD\\'

#Define o endereço de destino dos arquivos.
#path_destino = 'C:\\Users\\charlessodre\\Documents\\PastaVM\\Estudos\\OrganizadorArquivos\\DESTINO'
path_destino = 'D:\\FOTOS_POR_ANO\\'


In [4]:
# Define a Função para Cria um diretório, se não existir
def criar_diretorio(path, recursivo=False):
    if not os.path.exists(path):
        #print(novo_dir)
        if recursivo:
            os.makedirs(path)
        else:
            os.mkdir(path)

In [5]:
# Define a Função que retorna o ano do arquivo, primeiro tenta obter a data de modificação do arquivo, se não conseguir tenta a data de criação
def ano_arquivo(file):
      
    prop =os.stat(file)
    
    if prop.st_mtime > 0:
        data = prop.st_mtime
    elif prop.st_ctime > 0:
        data =  prop.st_ctime
        
    return datetime.datetime.fromtimestamp(data).year

In [6]:
#Define a função que retorna os segundos no formato hh:mm:ss
def formata_segundos_hhmmss(segundos):
    return time.strftime('%H:%M:%S', time.gmtime(segundos))

In [7]:
#Define a função que retorna da hora atual do sistema.
def get_hora_atual():
    return time.strftime("%H:%M:%S")

In [8]:
#Define a função que grava um arquivo TXT a partir de uma lista.
def grava_arquivo_log(lista_log, path_destino_log, modo_gravacao='w'):
    
    log_copia_arquivos = os.path.join(path_destino_log, "log_copia_arquivos.txt")
    
    with open(log_copia_arquivos, modo_gravacao, encoding='utf-8') as f:
        for s in lista_log:
            f.write(str(s) + '\n')

In [9]:
# Denfine a função que retorna um dicionário com a quantidade arquivos por diretório e a frequncia dos anos. 
def dic_arquivos_anos(path):
    
    qtd_arq_dir = {}

    for root, dirs, files in os.walk(path):
                              
        freq_ano = {}

        split_dir = root.split('\\')
        nome_dir = split_dir[len(split_dir)-1]

        anos_arq = [ano_arquivo(os.path.join(root, f)) for f in files]

        for ano in anos_arq:
            freq_ano[ano] = anos_arq.count(ano)


        qtd_arq_dir[root] = len(files), freq_ano, nome_dir
        
        #print("Root:", root)
        #print('Diretório:', nome_dir)
        #print('Qtd Arq: ', set(anos_arq))
        #print('Freq Ano: ',freq_ano)
        #print('----------------------------')
       

    return qtd_arq_dir

In [10]:
#Define a Função principal. 
def main ():
    
    
    #Variáveis de controle para debug
    habilitar_prints = True
    habilitar_gravacao_log = True
    habilitar_criacao_diretorios = True
    habilitar_copia_arquivos = True
    
    #Lista com as mensagens
    log_execucao = []
    arquivos_nao_copiados = []
    
    msg_arquivos_nao_copiados  = 'Não foi possível copiar o(s) arquivo(s) abaixo: '
    
    arquivos_nao_copiados.append(msg_arquivos_nao_copiados)
    
    # Armazena o total de arquivos não copiados.
    total_arquivos_nao_copiados = 0
        
    msg_inicio_execucao = '----------------------------------------------- Início Execução ----------------------------------------------- '
        
    log_execucao.append(msg_inicio_execucao)
    log_execucao.append('\n')
       
    #Data e hora atual
    hora_inicio = get_hora_atual()
       
    #Define o tempo de inicio da execução
    inicio = time.time()
    
    #Anos dos arquivos
    arquivos_anos = dic_arquivos_anos(path_origem)
    total_arquivos = 0
    
    #Percorre todos os diretórios do dicionário
    for key in arquivos_anos:      
        #Obtêm o diconário da frequencia de anos.
        dic_anos = arquivos_anos[key][1]
        
        #Verifica se o diretório está vazio, se estiver passa para o proximo.
        if len(dic_anos) == 0:
            continue
        
        #Obtêm a chave com maior valor
        anoComMaisArquivos = max(dic_anos, key=dic_anos.get)
        
        msg_inicio_copia = 'Copiando arquivos do diretório:[ %s ]'% key
        msg_ano_ocorrencia = 'Ano com maior acorrência: [ %d ]' % anoComMaisArquivos
        
        log_execucao.append(msg_inicio_copia)
        log_execucao.append(msg_ano_ocorrencia)
        
        if habilitar_prints:
            print(msg_inicio_copia)
            print(msg_ano_ocorrencia)
             
        dir_origem = os.path.abspath(key)
        msg_origem = 'Origem  <------ %s' % dir_origem
        
        log_execucao.append(msg_origem)
            
        if habilitar_prints:
            print(msg_origem)  
        
        # Monta o PATH de destino dos arquivos.
        dir_destino_ano = os.path.join(path_destino, str(anoComMaisArquivos)+'\\')      
        dir_destino = os.path.abspath(os.path.join(dir_destino_ano, key.replace(path_origem, dir_destino_ano) ))     
             
        msg_destino =  'Destino ------> %s' % dir_destino   
        
        log_execucao.append(msg_destino)
               
        if habilitar_prints:
            print(msg_destino)
        
        #Cria os diretórios
        if habilitar_criacao_diretorios:
            criar_diretorio(dir_destino, recursivo=True)
             
        arquivos = os.listdir(dir_origem)
               
        qtd_arq = 0
        
        #Percorre todos os arquivos do diretório
        for f in arquivos:
            
            path_arquivo = os.path.join(dir_origem, f)
            
            if(os.path.isfile(path_arquivo)):
                qtd_arq +=1
                total_arquivos += 1
                msg_log_arquivo = "Arq %d de %d |Nome: %s |Origem: %s | Hora Log: %s"   % (qtd_arq, arquivos_anos[key][0], f, path_arquivo, get_hora_atual())
                
                log_execucao.append(msg_log_arquivo)
               
                if habilitar_prints:
                    print(msg_log_arquivo) 
               
                #Copia os arquivos
                if habilitar_copia_arquivos:
                    try:
                        shutil.copy2(path_arquivo, dir_destino)
                    except  OSError as erro:
                        total_arquivos_nao_copiados += 1
                        arquivos_nao_copiados.append(path_arquivo + '| Erro: ' + str(erro))
                        
                        if habilitar_prints: 
                            print (msg_arquivos_nao_copiados)
                            print(erro)
                    
        
        log_execucao.append('\n')
        
        if habilitar_prints:   
            print('\n')
    
    #Define o tempo final da execução
    fim = time.time()
    
    #Mensagens de log 
    msg_fim_execucao = '----------------------------------------------- Fim Execução ----------------------------------------------- '
    
    msg_total_aquivos_origem = 'Total de diretórios copiados: %d' % len(arquivos_anos)
    msg_total_aquivos_copiados = 'Total de Arquivos copiados: %d' % total_arquivos
    msg_hora_inicio = 'Hora iníco: %s' % hora_inicio
    msg_hora_fim = 'Hora fim: %s'% get_hora_atual()
    msg_tempo_execucao = 'Tempo da Execução: %s' % formata_segundos_hhmmss(fim - inicio)
    
    msg_total_arquivos_nao_copiados = 'Total de arquivos não copiado(s): %d' % total_arquivos_nao_copiados
        
    log_execucao.append(msg_fim_execucao) 
    log_execucao.append('\n')
    log_execucao.append(msg_total_aquivos_origem)
    log_execucao.append(msg_total_aquivos_copiados)
    log_execucao.append(msg_hora_inicio)
    log_execucao.append(msg_hora_fim)  
    log_execucao.append(msg_tempo_execucao)
    
    log_execucao.append('\n')
    if total_arquivos_nao_copiados > 0:
        for naocopiado in arquivos_nao_copiados:
            log_execucao.append(naocopiado)      
        
    log_execucao.append(msg_total_arquivos_nao_copiados)
    
    if habilitar_prints:
        print(msg_fim_execucao)
        print(msg_total_aquivos_origem)
        print(msg_total_aquivos_copiados)
        print(msg_hora_inicio)
        print(msg_hora_fim)
        print(msg_tempo_execucao)
        print(msg_total_arquivos_nao_copiados)
   
    #Grava o arquivo de Log.
    if habilitar_gravacao_log:
        grava_arquivo_log(log_execucao, path_destino)

In [11]:
#Executa a função principal
main()

Copiando arquivos do diretório:[ C:\BACKUPS_FOTOS_CD\ ]
Ano com maior acorrência: [ 2019 ]
Origem  <------ C:\BACKUPS_FOTOS_CD\
Destino ------> D:\FOTOS_POR_ANO\2019\
Arq 1 de 1 |Nome: _copia_arquivos.bat |Origem: C:\BACKUPS_FOTOS_CD\_copia_arquivos.bat | Hora Log: 11:59:21


Copiando arquivos do diretório:[ C:\BACKUPS_FOTOS_CD\100OLYMP ]
Ano com maior acorrência: [ 2004 ]
Origem  <------ C:\BACKUPS_FOTOS_CD\100OLYMP
Destino ------> D:\FOTOS_POR_ANO\2004\100OLYMP
Arq 1 de 50 |Nome: P1010022.JPG |Origem: C:\BACKUPS_FOTOS_CD\100OLYMP\P1010022.JPG | Hora Log: 11:59:21
Arq 2 de 50 |Nome: P1010023.JPG |Origem: C:\BACKUPS_FOTOS_CD\100OLYMP\P1010023.JPG | Hora Log: 11:59:21
Arq 3 de 50 |Nome: P1010024.JPG |Origem: C:\BACKUPS_FOTOS_CD\100OLYMP\P1010024.JPG | Hora Log: 11:59:21
Arq 4 de 50 |Nome: P1010025.JPG |Origem: C:\BACKUPS_FOTOS_CD\100OLYMP\P1010025.JPG | Hora Log: 11:59:21
Arq 5 de 50 |Nome: P1010026.JPG |Origem: C:\BACKUPS_FOTOS_CD\100OLYMP\P1010026.JPG | Hora Log: 11:59:22
Arq 6 de 50 